<img src="image.jpg">

 # PyPRT - Building Modeling Optimization

This notebook is used to show how the Python bindings for PRT can be employed in optimizing the rule attributes of a generated model to achive predefined performance goals.

### Import PyPRT module and define paths-related functions

In [1]:
import sys, os

sys.path.append(os.path.join(os.getcwd(), "..", "src"))
from utility import visualize_PRT_results, combine_reports, summarize_matrix, summarize_report

SDK_PATH = os.path.join(os.getcwd(), "..", "install", "bin")
sys.path.append(SDK_PATH)

import pyprt

In [2]:
from scipy import optimize

In [3]:
CS_FOLDER = os.getcwd()
def asset_file(filename):
    return os.path.join(CS_FOLDER, filename)

In [4]:
print("\nInitializing PRT.")
pyprt.initialize_prt(SDK_PATH)

if not pyprt.is_prt_initialized():
    raise Exception("PRT is not initialized")


Initializing PRT.
[PRT] [2019-06-27 11:24:56] [info] Esri Procedural Runtime
[PRT] [2019-06-27 11:24:56] [info] Version: 2.0.5403 | Build Date: Tue 04/09/2019 10:26 AM | Build Config: PRT_BC_REL PRT_CC_OPT PRT_TC_VC141 | OS: win32 | ARCH: x86_64
[PRT] [2019-06-27 11:24:56] [debug] prtPlugins item 0: 'C:\Users\cami9495\Documents\esri-cityengine-sdk-master\examples\py4prt\Demo2_Optimization\..\install\lib'
[PRT] [2019-06-27 11:24:56] [error] failed to load library: error while loading library 'C:\Users\cami9495\Documents\esri-cityengine-sdk-master\examples\py4prt\Demo2_Optimization\..\install\lib\com.esri.prt.unreal.dll': The specified module could not be found.

[PRT] [2019-06-27 11:24:56] [warning] failed to load library com.esri.prt.unreal.dll
[PRT] [2019-06-27 11:24:56] [error] failed to load library: error while loading library 'C:\Users\cami9495\Documents\esri-cityengine-sdk-master\examples\py4prt\Demo2_Optimization\..\install\lib\DatasmithSDK.dll': The specified module could not 

In [1]:
from arcgis.gis import GIS

In [2]:
gis = GIS("https://www.arcgis.com", username="CLechot_zurich")

Enter password: ········


## Optimization Problem Definition

In this notebook, we are using a CGA rule that allows us to generate modern and sustainable buildings. The architecture of these buildings is focused on the green aspect of the building. Therefore, in addition to be modern and esthetical, the generated building answers also to the actual requirements of the city which are to encourage the integration of greenery on the buildings.

<img src="green_building.png">

### The variables

Among the values reported by the CGA rule, we want to optimize the __height of the generated building__. In this example, we would like the building height to be as close as possible to __10 meters__.
The next step is to define the inputs that will vary and on which we will optimize. These inputs must be CGA rule attributes. Here we will take the building height and the k factor as optimization inputs.

In [6]:
goal_str = "Building Height" # correspond to a CGA reported value

input_attr = ["buildingHeight:float","k:float"]
x0 = [13, 0.1] # input attributes initial value

In [7]:
shape_geo = asset_file("parcelN.obj") # parcel/geometry on which the model will be generated
mod = pyprt.ModelGenerator(shape_geo)

In [8]:
rpk = asset_file("simple_rule2.rpk")
rule_file_attr = "ruleFile:string=bin/simple_rule2.cgb"
start_rule_attr = "startRule:string=Default$Footprint"

In [9]:
def fct(x): # function to minimize
    input_val0 = input_attr[0]+"="+str(x[0])
    input_val1 = input_attr[1]+"="+str(x[1])
    
    generated_mod = mod.generate_model(rpk, [rule_file_attr, start_rule_attr, input_val0, input_val1])
    
    if len(generated_mod) == 1:
        rep = summarize_report(combine_reports(generated_mod[0]))
        #return rep[goal_str] # output to optimize : y
        return ((-10+rep[goal_str])*(-10+rep[goal_str]))

    else:
        print("Error in optimization process.")  

## Optimization Problem Resolution

In [46]:
bounds = [(0,25),(0,0.6)] # sequence of (min,max)

In [47]:
res = optimize.differential_evolution(fct, bounds)
res

     fun: 0.0
 message: 'Optimization terminated successfully.'
    nfev: 1053
     nit: 34
 success: True
       x: array([9.99999978, 0.47106757])

The set of attributes that minimizes the output is: __building height of 10 meters__ and __factor k of 0.47__.

### Conclusion and Visualization

In [9]:
generated_model = mod.generate_model(rpk, [rule_file_attr, start_rule_attr, input_attr[0]+"="+str(10), input_attr[1]+"="+str(0.47)])
if len(generated_model) == 1:
    print(summarize_report(combine_reports(generated_model[0])))

[PRT] [2019-06-27 09:39:57] [info] Using rule package C:\Users\cami9495\Documents\esri-cityengine-sdk-master\examples\py4prt\Demo2_Optimization\simple_rule2.rpk

[PRT] [2019-06-27 09:39:57] [debug] trying to read initial shape geometry from file:/C:%5CUsers%5Ccami9495%5CDocuments%5Cesri-cityengine-sdk-master%5Cexamples%5Cpy4prt%5CDemo2_Optimization%5CparcelN.obj
{'Building Height': 10.0, 'Id': 0.0, 'Parcel Area': 1780.0284423828125, 'Value': 1.7509000301361084}


In [11]:
exported_model = mod.generate_model(rpk, [rule_file_attr, start_rule_attr, input_attr[0]+"="+str(10), input_attr[1]+"="+str(0.47)],"com.esri.prt.codecs.OBJEncoder")

[PRT] [2019-06-27 09:18:09] [info] Using rule package C:\Users\cami9495\Documents\esri-cityengine-sdk-master\examples\py4prt\Demo2_Optimization\simple_rule2.rpk

[PRT] [2019-06-27 09:18:09] [debug] trying to read initial shape geometry from file:/C:%5CUsers%5Ccami9495%5CDocuments%5Cesri-cityengine-sdk-master%5Cexamples%5Cpy4prt%5CDemo2_Optimization%5CparcelN.obj


In [26]:
from PyGEL3D import gel
from PyGEL3D import js

os.chdir("../output")
js.set_export_mode()
m = gel.obj_load("theModel_0.obj")

Visualization in a separate window:

In [24]:
viewer = gel.GLManifoldViewer()
viewer.display(m) # press ESC to go back to the script

In [12]:
viewer.event_loop()

In [25]:
del viewer

Visualization in a notebook cell:

In [27]:
js.display(m, smooth=False, wireframe=False)

Save the glTF model on ArcGIS Online (possible to download it from there)

In [ ]:
exported_GLTF= mod.generate_model(rpk, [rule_file_attr, start_rule_attr, input_attr[0]+"="+str(10), input_attr[1]+"="+str(0.47)],"com.esri.prt.codecs.GLTFEncoder")

In [4]:
GLTF_item = gis.content.add({'title':'Test','type':"Service Definition"}, data='theModel_0.glb', folder='packages')

In [ ]:
display(GLTF_item)

##### Optimization with envelope.rpk ==> too slow for the moment

In [5]:
goal_str_green = "green area" # correspond to a CGA reported value

input_attr_green = ["lot_coverage_parameter:float"]
x0_green = [10]

In [6]:
rpk_green = asset_file("envelope1806.rpk")
rule_file_attr_green = "ruleFile:string=rules/typology/envelope.cgb"
start_rule_attr_green = "startRule:string=Default$Lot"

In [63]:
def fct_green(x):
    input_val0 = input_attr_green[0]+"="+str(x[0])
    generated_mod = mod.generate_model(rpk_green, [rule_file_attr_green, start_rule_attr_green, input_val0])
    
    if len(generated_mod) == 1:
        rep = summarize_report(combine_reports(generated_mod[0]))
        return -rep[goal_str_green]
    else:
        print("Error in optimization process.")

In [64]:
bounds_green = [(0,100)]

Test

In [65]:
fct_green(x0_green)

-1239.515014410019

res_green = optimize.differential_evolution(fct_green, bounds_green) # shgo
res_green

In [68]:
print("\nShutdown PRT.")
pyprt.shutdown_prt()


Shutdown PRT.
